In [12]:
## pip install striprtf tiktoken openai
import os
from striprtf.striprtf import rtf_to_text
import pandas as pd
import numpy as np
import re
import tiktoken
import openai
from openai.embeddings_utils import get_embedding
from sklearn.metrics.pairwise import cosine_similarity
import time
import json

model='text-embedding-ada-002'

openai.api_key =  '**'
tokensUsed = 0

In [70]:
string_to_process = "Well, my name is Alice D. That’s my married name, of course, my maiden name was S., Alice S. and I was born in Belfast. My father died when I was only two years old so my very young mother, twenty-three, was a widow. My brother was born after he died and she brought the three of us up. In those days, there was no widow’s pensions or anything like that so it was all hard work. How old was your sister when your father died? She would have been three. So she had three children under four? Yes, she was three, I was two, and my brother was born three weeks after my father died. Well, that was where we grew up in Belfast and when I started work, I started a very interesting job. I loved it, making chocolates. I started with a small firm, first of all, Thompsons of Belfast, but I moved from there to the Ormeau Bakery in 1939, the war years, you know and I was there from thirty nine to fifty three, when I got married and went to Canada. And then we stayed in Canada for four years, which I loved. We’d good jobs, everything went well, but I couldn’t stand the humidity and the heat in the summer time so we came back. However, my time in the Ormeau Baker I would say were amongst the happiest years; they were all happy. They were very special years. I think it was because it was wartime. How old were you when you started work? I was twenty-six when I went into the Ormeau Bakery and I was forty when we left to go to Canada. And you see I wasn’t married until I was forty. Sensible woman, you waited. [Both laugh] Well, in the war years you know, nobody could get married because there were coupons, and everything was rationed, and jobs were queer, people were having to go and work in ammunition places. I was one of the fortunate people who had a nice job and a job that I wasn’t very willing to give up to go to Canada. But then, I wanted to go and the time was right. So once the war was over, you see, and a few years over, things got on and got back to normal. But the war years in the Ormeau Bakery were very very interesting years indeed, because it was food, you see. I mean my speciality was making chocolates, which of course involved the parcels for troops and all that kind of thing, because all the sales went through the bread servers. So they would place orders with me for em, oh maybe several dozen half pound boxes of peppermint creams. These were all going into different packages for soldiers, you know people sending them, but the bakery itself, the bakery supplied the bread when ships came in, but it was all very hush hush, you see. The names of the"
import nltk
nltk.download('punkt')
from nltk.corpus import stopwords
from nltk.stem import WordNetLemmatizer
nltk.download('stopwords')
nltk.download('wordnet')
nltk.download('omw-1.4')


import string
 

[nltk_data] Downloading package punkt to /home/colbn1/nltk_data...
[nltk_data]   Package punkt is already up-to-date!
[nltk_data] Downloading package stopwords to /home/colbn1/nltk_data...
[nltk_data]   Package stopwords is already up-to-date!
[nltk_data] Downloading package wordnet to /home/colbn1/nltk_data...
[nltk_data]   Package wordnet is already up-to-date!
[nltk_data] Downloading package omw-1.4 to /home/colbn1/nltk_data...
[nltk_data]   Package omw-1.4 is already up-to-date!


In [141]:
def countTokens(text):
    encoding = tiktoken.get_encoding('cl100k_base')
    return len(encoding.encode(text))

def askGPT(messages):
    try: 
        tokens = 0
        for value in messages:
            tokens += countTokens(value['content'])


        response = {}

        if(tokens < 3000):

            completion = openai.ChatCompletion.create(
                    model="gpt-3.5-turbo",
                    messages=messages
                )
            responseText = completion.choices[0].message.content
            tokens += countTokens(responseText)

            response = {
                "response": responseText ,
                "tokens": tokens

            }

        else:
            response = {
                "error": "too many tokens"
            }

        return response
    except Exception as e:
        print("ERROR OCCURED IN GPT FETCH" + str(e))
        print("Waiting 10 seconds and trying again...")
        time.sleep(10)
        askGPT(messages)

    
def remove_punctuation(text):
    # Create a translation table to remove punctuation
    translator = str.maketrans('', '', string.punctuation + "’")
    
    # Use the translation table to remove punctuation from the text
    return text.translate(translator)

def preprocess_text(text):
    # Lowercase the text
    text = text.lower()

   

    # Expand contracted words
    # You can create your own mapping or use third-party libraries for this step

    pattern = r"\[.*?\]"
    
    # Use re.sub() to replace all occurrences of [ *** ] with an empty string
    cleaned_text = re.sub(pattern, "", text)
    
    # Tokenize the text into individual words
    words = nltk.word_tokenize(cleaned_text)
    
    
    # Remove stop words
    # stop_words = set(stopwords.words('english'))
    # words = [word for word in words if word not in stop_words]
   
    # Lemmatize the words
    # lemmatizer = WordNetLemmatizer()
    # words = [lemmatizer.lemmatize(word) for word in words]
    # Join the words back into a single string
    text = ' '.join(words)
    
    sentences = text.split(" . ")
    
    #Remove punctuation and special characters
    text = [remove_punctuation(text) for text in sentences]
    
    text = [s for s in text if s.strip()]
    
    text = ' '.join(text)
    
    
    return text

def break_string_into_chunks(text, words_per_chunk):
    words = text.split()
    chunks = []
    current_chunk = []

    for word in words:
        current_chunk.append(word)

        if len(current_chunk) >= words_per_chunk:
            chunks.append(" ".join(current_chunk))
            current_chunk = []

    # Add the remaining words as the last chunk
    if current_chunk:
        chunks.append(" ".join(current_chunk))

    return chunks

In [135]:

processed_string = preprocess_text(string_to_process)
print(processed_string)


well  my name is alice d that  s my married name  of course  my maiden name was s  alice s and i was born in belfast my father died when i was only two years old so my very young mother  twentythree  was a widow my brother was born after he died and she brought the three of us up in those days  there was no widow  s pensions or anything like that so it was all hard work how old was your sister when your father died  she would have been three so she had three children under four  yes  she was three  i was two  and my brother was born three weeks after my father died well  that was where we grew up in belfast and when i started work  i started a very interesting job i loved it  making chocolates i started with a small firm  first of all  thompsons of belfast  but i moved from there to the ormeau bakery in 1939  the war years  you know and i was there from thirty nine to fifty three  when i got married and went to canada and then we stayed in canada for four years  which i loved we  d goo

In [145]:
def get_embedding(text, model="text-embedding-ada-002"):
   text = " ".join(" ".join(text).split()[:100])
   text = text.replace("\n", " ")
   return openai.Embedding.create(input = [text], model=model)['data'][0]['embedding']








dataSnippets = pd.DataFrame(columns=["INTERVIEW_FILE_NAME", "TEXT_SNIPPET", "EMBEDDING"])

directory_path = 'data'


cum_tokens = 0

start_time = time.time()
codesMap = {}
counter = 0
for filename in os.listdir(directory_path):
    if filename.endswith('.rtf'):  # check if file is an RTF file
        file_path = os.path.join(directory_path, filename)
        with open(file_path, 'r') as file:
            if(filename == "SWW01.rtf"):
                rtf_text = file.read()
                plain_text = rtf_to_text(rtf_text)  # convert RTF to plain text

               
                pattern = r"AD:\s+.*"

                # Remove dialogue blocks from the text
                cleaned_text = re.findall(pattern, plain_text)
                cleaned_text = " ".join(cleaned_text)
                cleaned_text = cleaned_text.replace("AD:", "").replace("\t", "")
                if j <1:
                    processed_text = preprocess_text(cleaned_text)
                    
                    encoding = tiktoken.get_encoding('cl100k_base')

                    num_tokens = len(encoding.encode(processed_text))

                    cumulative_tokens += num_tokens

                    totalLeft = len(processed_text)
                    chunks = break_string_into_chunks(processed_text, 200)
                    print(len(chunks))
                    for index, chunk in enumerate(chunks):
                       
                        
                        systemContent = """
                            You are a researcher researching the experiences of women who lived through World War II. 
                            You are reading an interview transcript and trying to find thematic codes which encapsulate the 
                            experience of women in a summative, salient, and essence-capturing summary of the transcript. The purpose
                            of the codes is to form the basis of research findings on how the war impacted women.
                        """

   
                        questionContent = f"""You will receive a part of the interview transcript with an interviewee who participated in 
                        the research. Based on the transcript, identify 4 codes which 
                        can be derived from direct quotes in the transcript and which highlight how the war impacted women in a summative, salient, 
                        and essence-capturing way. Under each code, include some elaboration of what the code means as a description. The codes 
                        should describe generalizable phenomena so that they can be compared to other interviewees and eg. named entities should be mentioned as their generalizable categories. Here is the transcript: "{chunk}".
                        In your response, include nothing but 10 codes and their descriptions as a json object in the following format: 

                                    {{ "1": {{"title": title_of_code, "description": description_of_code}}, ...}}
                         """
    
                        messages = [
                                {'role': 'system', 'content': systemContent},
                          #      {"role": "assistant", "content": assistantContent},
                                {'role': 'user', 'content': questionContent}
                            ]

                        completion = askGPT(messages)
                        
                        response = completion['response']
                        
                        num_tokens = completion['tokens']
                        cum_tokens += num_tokens
        
                        print("TOKENS USED: " + str(num_tokens))
                        
                        print("CUMULATIVE TOKENS USED: " + str(cum_tokens/ 1000) + "K")

                        print(response)

                        codes = {}
                        try:
                            codes = json.loads(response)
                        except json.JSONDecodeError:
                            print("ERROR EXTRACTING JSON OBJECT FROM RESPONSE STRING")
                            codes = {"Error": "True", "JSONstring": response}

                        codesMap[index] = {
                            "text": chunk,
                            "codes": codes
                        }
                        counter += 1
                        print("DONE: " + str(counter))

# Specify the text file path
text_file = 'codes.txt'

# Open the text file in write mode
with open(text_file, mode='w') as file:
    json.dump(codesMap, file, ensure_ascii=False)
                        
                        #print("EMBEDDING SNIPPET: " + item)
                        #embedding = get_embedding(item)
                        #row = pd.Series({"INTERVIEW_FILE_NAME": filename, "TEXT_SNIPPET": item, "EMBEDDING": embedding})
                        #dataSnippets = pd.concat([dataSnippets, row.to_frame().T], ignore_index=True)
                        #totalLeft -= 1
                        #print("EMBEDDINGS LEFT IN FILE: " + filename +  " ### " + str(totalLeft))

            
elapsed_time = time.time() - start_time

print("TOTAL TOKENS IN ALL FILES: " + str(cumulative_tokens))
print("Computation took " + str(elapsed_time / 60) + "minutes" )

#dataSnippets.to_csv('embedded_snippets.csv', index=False)
        




69
TOKENS USED: 779
CUMULATIVE TOKENS USED: 0.779K
{ 
  "1": {
    "title": "Single mothers' resilience and resourcefulness",
    "description": "This code captures the experiences of single mothers during World War II who had to provide for their children without the support of widow's pensions. These women faced the challenges of raising a family on their own and relied on hard work and determination to make ends meet."
  },
  "2": {
    "title": "Impact of parental loss",
    "description": "This code represents the experiences of women who lost their fathers at a young age, adding an additional burden to their mothers who had to raise them alone. It signifies the emotional and financial impact of parental loss on these women and their families."
  },
  "3": {
    "title": "Opportunities for women in the workforce",
    "description": "This code highlights the employment opportunities that opened up for women during the war years. It focuses on the interviewee's love for her job mak

TOKENS USED: 730
CUMULATIVE TOKENS USED: 5.834K
{
  "1": {
    "title": "Blackout and fear of overhead attacks",
    "description": "Women experienced a pitch-black environment during the war and were only allowed a flashlamp switched to the ground due to the fear of overhead attacks. This created a sense of unease and strangeness in their daily lives."
  },
  "2": {
    "title": "Canteens and social activities",
    "description": "Canteens were set up in hotels, church halls, and other places, providing opportunities for socializing, parties, dances, and dates. These activities brought some enjoyment and relief during the war for women and the troops."
  },
  "3": {
    "title": "Efforts to improve soldiers' well-being",
    "description": "The establishment of canteens and social activities aimed to make life more livable for the soldiers who were far away from home. These efforts were made by various branches of the military, including the airforce, navy, and army."
  },
  "4": {
 

TOKENS USED: 648
CUMULATIVE TOKENS USED: 10.239K
{"1": {"title": "Opportunity limitations", "description": "Women experienced limited opportunities for education and career advancement during the war. This was especially evident in the lack of options for higher education and professional paths."},
"2": {"title": "Migration as a means of escape", "description": "Women sought opportunities abroad, such as moving to Canada, as a way to escape the hardships and constraints of war. Marriage often served as a means to enable this migration."},
"3": {"title": "Limited agency in decision-making", "description": "Women had limited agency in making important life decisions, such as going to work or pursuing their education. Social and economic pressures often influenced these decisions."},
"4": {"title": "Constrained social mobility", "description": "The war resulted in restricted social mobility for women, hindering their ability to pursue their goals and aspirations. Access to higher educatio

TOKENS USED: 654
CUMULATIVE TOKENS USED: 15.84K
{
  "1": {
    "title": "Gender roles and work opportunities",
    "description": "The war created new work opportunities for women, allowing them to take on roles traditionally held by men and gain experience and promotions."
  },
  "2": {
    "title": "Discrimination and favoritism",
    "description": "Women faced discrimination in the workplace, with favoritism towards men for promotions and limited employment opportunities for family members."
  },
  "3": {
    "title": "Importance of skill and experience",
    "description": "Skill and experience were valued attributes for women seeking job opportunities during the war, leading to advancements and better chances of employment."
  },
  "4": {
    "title": "Challenges of getting hired",
    "description": "Securing employment during the war was a significant challenge for women, with the emphasis on 'getting in' and limited positions available."
  }
}
DONE: 22
TOKENS USED: 703
CUMULAT

TOKENS USED: 1024
CUMULATIVE TOKENS USED: 21.056K
{ 
  "1": {
    "title": "Overcoming fear and building confidence",
    "description": "Women participants in the war often gained confidence and overcame their fear of facing people through their various tasks and responsibilities. They were chosen based on their capabilities, appearance, and work ethic, and received compliments for their contributions."
  },
  "2": {
    "title": "Multiple work locations",
    "description": "Women had the experience of working at different locations during the war, such as Cornmarket, Anne Street, Donegall Place, and Antrim Road. This highlights the flexibility and adaptability required by women during the war."
  },
  "3": {
    "title": "Enjoyment of work",
    "description": "The interviewee expresses that her work during the war was never a chore and she always enjoyed it. This suggests a sense of fulfillment and satisfaction in their tasks and responsibilities."
  },
  "4": {
    "title": "Impor

TOKENS USED: 720
CUMULATIVE TOKENS USED: 25.754K
{
  "1": {
    "title": "Sacrifices and obligations",
    "description": "Women experienced the impact of war through the sacrifices and obligations placed on their loved ones who had to join the military, leading to absences and restrictions on their daily lives."
  },
  "2": {
    "title": "Adaptation to blackouts and air raids",
    "description": "Women had to adjust to the challenges posed by blackouts and air raids. Seeking safety in air raid shelters and constantly moving from one shelter to another became a regular part of their lives during the war."
  },
  "3": {
    "title": "Supporting soldiers through companionship",
    "description": "Women provided emotional support and companionship to soldiers stationed in barracks by hosting them in their homes and providing them with enjoyable activities and home-cooked meals, which offered a break from the monotonous barracks routine."
  },
  "4": {
    "title": "Nourishing soldiers 

TOKENS USED: 665
CUMULATIVE TOKENS USED: 29.264K
{
  "1": {
    "title": "Limited knowledge of war",
    "description": "Women had limited knowledge about the details and events of the war. They relied on hearsay and occasional conversations with soldiers for information."
  },
  "2": {
    "title": "Restricted social interactions",
    "description": "Women faced restrictions in their social interactions with soldiers. They were cautious about spending time with soldiers due to the fear of consequences and restrictions placed on them."
  },
  "3": {
    "title": "Desire for companionship",
    "description": "Women expressed a desire for companionship and the opportunity to socialize with soldiers. However, they were aware of the potential negative consequences and trade-offs."
  },
  "4": {
    "title": "Sense of loss and sadness",
    "description": "Women experienced a sense of loss and sadness in relation to the war, as it brought restrictions and limitations on their interactions

TOKENS USED: 616
CUMULATIVE TOKENS USED: 33.684K
{
  "1": {
    "title": "Fear and Anxiety",
    "description": "Women experienced fear and anxiety during air raids, resulting in distressing dreams and emotional reactions."
  },
  "2": {
    "title": "Resilience",
    "description": "Women showed resilience by managing to continue working despite injuries sustained during the war."
  },
  "3": {
    "title": "Concern for Safety",
    "description": "Mothers expressed concern for the safety of their daughters and urged them to stay home for their own protection."
  },
  "4": {
    "title": "Supportive Community",
    "description": "Women received support from their families and local air raid wardens during difficult times."
  }
}
DONE: 46
TOKENS USED: 662
CUMULATIVE TOKENS USED: 34.346K
{
  "1": {
    "title": "Perseverance and Resilience",
    "description": "Women facing the risk of bombings and personal harm continued to go to work, despite their fear, and showed determination in c

TOKENS USED: 639
CUMULATIVE TOKENS USED: 39.238K
{
  "1": {
    "title": "Financial Sacrifice",
    "description": "Women had to pay for their involvement in various activities such as guide competitions, camping, and excursions."
  },
  "2": {
    "title": "Support from Community",
    "description": "Women received financial support and resources from their community to participate in guide activities."
  },
  "3": {
    "title": "Inclusion of Non-religious Affiliated Women",
    "description": "The interviewee's guide company was not attached to a church, highlighting the inclusion of women from various religious backgrounds."
  },
  "4": {
    "title": "Quality Leadership",
    "description": "The guide company had a very good captain and lieutenant from a well-known school, indicating the importance of strong leadership in guiding."
  }
}
DONE: 54
TOKENS USED: 645
CUMULATIVE TOKENS USED: 39.883K
{
  "1": {
    "title": "Impact on Childhood",
    "description": "The war disrupted t

TOKENS USED: 720
CUMULATIVE TOKENS USED: 44.733K
{
  "1": {
    "title": "Gendered division in education",
    "description": "During World War II, there was a clear gendered division in education, with boys and girls sitting separately in class. While most teachers were female, there was usually one male headmaster who was considered to be highly intelligent."
  },
  "2": {
    "title": "Financial constraints and resourcefulness",
    "description": "Wages were very low during the war, causing financial constraints for women. A common example of resourcefulness was the practice of using both sides of a page in a jotter to save money and avoid waste."
  },
  "3": {
    "title": "Closeness and mutual support within communities",
    "description": "Women described a close-knit community during World War II, with neighbors being very supportive of each other. Doors were often open for assistance and camaraderie."
  },
  "4": {
    "title": "Inter-generational connection in education",
  

In [146]:
with open('codes.txt', 'r+') as file:
    data =file.read()
    json_data = json.loads(data)
        
    for snippetId in list(json_data.keys()):
        print("Working on snippet " + snippetId)
        
        for codeId in list(json_data[snippetId]['codes'].keys()):
            print("working on code Id " + codeId)
            description = json_data[snippetId]['codes'][codeId]['description']
            embedding = get_embedding(description)
            json_data[snippetId]['codes'][codeId]['embedding'] = embedding
            print("embedded.")
            
    file.truncate(0)
    file.seek(0)
    json.dump(json_data, file, ensure_ascii=False)
    
    print("Data saved into codes.txt")


Working on snippet 0
working on code Id 1
embedded.
working on code Id 2
embedded.
working on code Id 3
embedded.
working on code Id 4
embedded.
Working on snippet 1
working on code Id 1
embedded.
working on code Id 2
embedded.
working on code Id 3
embedded.
working on code Id 4
embedded.
Working on snippet 2
working on code Id 1
embedded.
working on code Id 2
embedded.
working on code Id 3
embedded.
working on code Id 4
embedded.
Working on snippet 3
working on code Id 1
embedded.
working on code Id 2
embedded.
working on code Id 3
embedded.
working on code Id 4
embedded.
Working on snippet 4
working on code Id 1
embedded.
working on code Id 2
embedded.
working on code Id 3
embedded.
working on code Id 4
embedded.
Working on snippet 5
working on code Id 1
embedded.
working on code Id 2
embedded.
working on code Id 3
embedded.
working on code Id 4
embedded.
Working on snippet 6
working on code Id 1
embedded.
working on code Id 2
embedded.
working on code Id 3
embedded.
working on code 

embedded.
Working on snippet 50
working on code Id 1
embedded.
working on code Id 2
embedded.
working on code Id 3
embedded.
working on code Id 4
embedded.
working on code Id 5
embedded.
working on code Id 6
embedded.
Working on snippet 51
working on code Id 1
embedded.
working on code Id 2
embedded.
working on code Id 3
embedded.
working on code Id 4
embedded.
Working on snippet 52
working on code Id 1
embedded.
working on code Id 2
embedded.
working on code Id 3
embedded.
working on code Id 4
embedded.
Working on snippet 53
working on code Id 1
embedded.
working on code Id 2
embedded.
working on code Id 3
embedded.
working on code Id 4
embedded.
Working on snippet 54
working on code Id 1
embedded.
working on code Id 2
embedded.
working on code Id 3
embedded.
working on code Id 4
embedded.
Working on snippet 55
working on code Id 1
embedded.
working on code Id 2
embedded.
working on code Id 3
embedded.
working on code Id 4
embedded.
Working on snippet 56
working on code Id 1
embedded.

In [147]:
# [id, title, description, embedding, quotes, text]
import uuid

df = pd.DataFrame(columns=["ID", "TITLE", "DESCRIPTION", "EMBEDDING"])



    

with open('codes.txt', 'r') as file:
    data =file.read()
    json_data = json.loads(data)
        
    for snippetId in list(json_data.keys()):
        for codeId in list(json_data[snippetId]['codes'].keys()):
            code = json_data[snippetId]['codes'][codeId]
            print(code)
            new_row = {
                "ID": uuid.uuid4().hex,
                "TITLE": code['title'],
                "DESCRIPTION": code['description'],
                "EMBEDDING": code['embedding'],
            }
            print(new_row)
            df = df.append(new_row, ignore_index=True)

            
df.to_csv('codes.csv', index=False)          
            
            
           
            

{'title': "Single mothers' resilience and resourcefulness", 'description': "This code captures the experiences of single mothers during World War II who had to provide for their children without the support of widow's pensions. These women faced the challenges of raising a family on their own and relied on hard work and determination to make ends meet.", 'embedding': [0.0017676412826403975, -0.006476880516856909, 0.009634851478040218, -0.027109196409583092, -0.01014985516667366, 0.02932657115161419, -0.025063490495085716, -0.00915561243891716, -0.004584959242492914, -0.029026152566075325, -0.003343944437801838, 0.033847156912088394, -0.0037087383680045605, 0.0179106667637825, 0.013847864232957363, -0.004270235076546669, 0.02698044665157795, 0.00769643671810627, -0.0020206724293529987, -0.022517085075378418, -0.016866356134414673, -0.015779126435518265, 0.0004930977011099458, 0.003197311656549573, -0.010929512791335583, -0.032187700271606445, -0.00019290267664473504, -0.0282965656369924

/tmp/ipykernel_138/2321534149.py:25: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df = df.append(new_row, ignore_index=True)
/tmp/ipykernel_138/2321534149.py:25: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df = df.append(new_row, ignore_index=True)
/tmp/ipykernel_138/2321534149.py:25: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df = df.append(new_row, ignore_index=True)
/tmp/ipykernel_138/2321534149.py:25: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df = df.append(new_row, ignore_index=True)
/tmp/ipykernel_138/2321534149.py:25: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future versio

{'title': 'Impact of parental loss', 'description': 'This code represents the experiences of women who lost their fathers at a young age, adding an additional burden to their mothers who had to raise them alone. It signifies the emotional and financial impact of parental loss on these women and their families.', 'embedding': [-0.003494606353342533, -0.00655060401186347, 0.0029240583535283804, -0.019370103254914284, -0.0065648676827549934, 0.007730924990028143, -0.027443358674645424, -0.015404795296490192, 0.004186396021395922, -0.020425617694854736, 0.011895925737917423, 0.028955310583114624, -0.023121457546949387, 0.016075190156698227, -0.0015208669938147068, -0.008037595078349113, 0.03152277693152428, 0.012773143127560616, -0.002037926111370325, -0.03942486643791199, -0.00039916072273626924, -0.015205103904008865, -0.002672660630196333, 0.006126258987933397, -0.019740959629416466, -0.027799950912594795, 0.009820557199418545, -0.026787227019667625, 0.015390532091259956, -0.03063842654

/tmp/ipykernel_138/2321534149.py:25: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df = df.append(new_row, ignore_index=True)
/tmp/ipykernel_138/2321534149.py:25: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df = df.append(new_row, ignore_index=True)
/tmp/ipykernel_138/2321534149.py:25: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df = df.append(new_row, ignore_index=True)
/tmp/ipykernel_138/2321534149.py:25: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df = df.append(new_row, ignore_index=True)
/tmp/ipykernel_138/2321534149.py:25: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future versio

{'title': 'Shifted Responsibilities', 'description': 'Women took on new roles and responsibilities, such as knitting for the military, in support of the war effort.', 'embedding': [-0.01711493916809559, -0.01756093092262745, -0.0021794370841234922, -0.04284309968352318, 0.00922645814716816, 0.0019337930716574192, -0.009937257505953312, -0.008808339945971966, 0.0008162000449374318, -0.031358808279037476, 0.018313543871045113, 0.025644535198807716, -2.9480544981197454e-05, 0.008815309032797813, -0.003637621644884348, -0.002707310253754258, 0.03963753208518028, 0.029965082183480263, 0.012829235754907131, -0.045379675924777985, -0.007979074493050575, -0.007623674347996712, 0.008724716491997242, 0.0212264284491539, -0.009080116637051105, -0.029379718005657196, 0.01988845132291317, -0.03807656094431877, 0.02777693420648575, -0.048696741461753845, -0.02001388743519783, 0.016459889709949493, -0.012285683304071426, -0.038801297545433044, -0.037519071251153946, -0.019846640527248383, -3.79191114

...

/tmp/ipykernel_138/2321534149.py:25: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df = df.append(new_row, ignore_index=True)
/tmp/ipykernel_138/2321534149.py:25: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df = df.append(new_row, ignore_index=True)
/tmp/ipykernel_138/2321534149.py:25: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df = df.append(new_row, ignore_index=True)
/tmp/ipykernel_138/2321534149.py:25: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df = df.append(new_row, ignore_index=True)
/tmp/ipykernel_138/2321534149.py:25: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future versio

{'title': 'High Standing and Proof', 'description': 'This code emphasizes the importance of personal reputation and status in the workplace during the war, particularly for women, and how it provided a sense of validation and affirmation.', 'embedding': [-0.014134417288005352, -0.004231667146086693, 0.007334168069064617, -0.032208289951086044, -0.0053103272803127766, 0.02409849688410759, -0.03457484766840935, -0.0015314089832827449, -0.0056350077502429485, -0.01946639083325863, 0.011414317414164543, 0.027114415541291237, -0.015007446520030499, 0.023420274257659912, -0.0027688017580658197, -0.016104144975543022, 0.025743544101715088, -0.0078428341075778, 0.005180455278605223, -0.030332358554005623, -0.009163200855255127, -0.00011189070937689394, -0.006046269554644823, 0.008398397825658321, -0.009184845723211765, -0.00735220592468977, 0.020490936934947968, -0.03950998932123184, 0.01207810826599598, -0.02001473866403103, -0.018672727048397064, 0.0009947845246642828, -0.009394084103405476,

/tmp/ipykernel_138/2321534149.py:25: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df = df.append(new_row, ignore_index=True)
/tmp/ipykernel_138/2321534149.py:25: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df = df.append(new_row, ignore_index=True)
/tmp/ipykernel_138/2321534149.py:25: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df = df.append(new_row, ignore_index=True)
/tmp/ipykernel_138/2321534149.py:25: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df = df.append(new_row, ignore_index=True)
/tmp/ipykernel_138/2321534149.py:25: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future versio

{'title': 'Assistance from soldiers', 'description': 'The soldiers present at the incident helped the interviewee by getting her out of the hole and fixing her bike. This code illustrates the role of soldiers in providing assistance and support to women during challenging situations caused by the war.', 'embedding': [0.011280424892902374, 0.014386222697794437, 0.00985021609812975, -0.02560354955494404, -0.010656461119651794, 0.015241543762385845, -0.016769904643297195, -0.015367738902568817, -0.005233584437519312, -0.02453790418803692, 0.025182900950312614, 0.01580240949988365, -0.01632121205329895, 0.026627130806446075, 0.003014656715095043, -0.008160606026649475, 0.023570409044623375, 0.022462697699666023, 0.023360084742307663, -0.022616935893893242, -0.02598213590681553, -0.009576793760061264, 0.012254930101335049, -0.0027745359111577272, -0.008293811231851578, -0.0184665247797966, 0.015017197467386723, -0.0355028435587883, 0.02582789771258831, -0.027552561834454536, -0.028435925021

/tmp/ipykernel_138/2321534149.py:25: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df = df.append(new_row, ignore_index=True)
/tmp/ipykernel_138/2321534149.py:25: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df = df.append(new_row, ignore_index=True)
/tmp/ipykernel_138/2321534149.py:25: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df = df.append(new_row, ignore_index=True)
/tmp/ipykernel_138/2321534149.py:25: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df = df.append(new_row, ignore_index=True)
/tmp/ipykernel_138/2321534149.py:25: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future versio

In [148]:
df = pd.read_csv('codes.csv')

df['EMBEDDING'] = df['EMBEDDING'].apply(eval).apply(np.array, dtype=float)

embeddings = np.array(df['EMBEDDING'].tolist())
print(embeddings)

[[ 0.00176764 -0.00647688  0.00963485 ... -0.02619364  0.00729588
  -0.00381245]
 [-0.00349461 -0.0065506   0.00292406 ... -0.02038283  0.00533819
  -0.00697852]
 [-0.01269483 -0.01090336  0.00617178 ... -0.01514668  0.02064051
  -0.01666416]
 ...
 [-0.017008   -0.01407323  0.00523481 ... -0.00483895  0.00975981
  -0.01047644]
 [-0.02151632 -0.02866983 -0.00891052 ... -0.01644053  0.01074421
  -0.00832485]
 [-0.01555542 -0.0213887   0.00729505 ...  0.00180997  0.01391438
  -0.01162519]]


In [154]:
from sklearn.cluster import KMeans
import ast

matrix = np.vstack(df.EMBEDDING.values)
n_clusters = 70

kmeans = KMeans(n_clusters = n_clusters, init='k-means++', random_state=42)
kmeans.fit(matrix)
df['CLUSTER'] = kmeans.labels_

cluster_groups = df.groupby('CLUSTER')

for cluster_label, cluster_data in cluster_groups:
    print(f"Cluster {cluster_label}:")
    for index, row in cluster_data.iterrows():
        print(row['TITLE'] + ": " + row['DESCRIPTION'])
        
    
    print('\n')

Cluster 0:
Strict time discipline: Women were required to adhere to strict time schedules, clock in on time, and face consequences if they were late. This discipline was enforced to maintain efficiency and productivity.


Cluster 1:
Impact of bombings on daily life: Women experienced the constant threat of bombings and had to find ways to ensure their safety. Shelters were limited, so some women sought refuge in the mountains, which they believed offered more protection than traditional shelters.
Professional Shifts: Women had to change their career paths during the war due to the impact on industries. For example, the interviewee's sister shifted from stitching in a clothing company to working in a bakery shop and later a fashion store.
Resource Management: Women had to carefully manage resources during the war. This included calculating ingredient quantities, minimizing loss, and maintaining efficient inventory management. The war necessitated resourcefulness and efficient allocation